# Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper_env`.

Activate it.

You will find more info about virtual environments in the course content and on the web.

## API Scraping

### A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword.

NOTE: external libraries need to be installed first. Check their documentation.

Check the [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the Requests documentation to:
1. use the `get()` method to connect to this endpoint: https://country-leaders.onrender.com/status
2. check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is the signification of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [1]:
# import the requests library (1 line)
import requests

# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = "https://country-leaders.onrender.com"

# assign the /status endpoint to another variable called status_url (1 line)
status_url = f"{root_url}/status"

# query the /status endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(status_url)

# check the status_code using a condition and print appropriate messages (4 lines)
if req.status_code == 200:
    print(req.text)
else:
    print(f"Status Code: {req.status_code}")

"Alive"


### Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. Check what to do in the Requests [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/).


In [2]:
# Set the countries_url variable (1 line)
countries_url = f"{root_url}/countries"

# query the /countries endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(countries_url)

# Get the JSON content and store it in the countries variable (1 line)
countries = req.json()

# display the request's status code and the countries variable (1 line)
print(req.status_code, countries)

403 {'message': 'The cookie is missing'}


### Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [6]:
# !!! 2 LINES !!!
# Set the cookie_url variable (1 line)
cookie_url = f"{root_url}/cookie"

# Query the enpoint, set the cookies variable and display it (2 lines)
req = requests.get(cookie_url)
cookies = req.cookies
print(cookies)

<RequestsCookieJar[<Cookie user_cookie=236cfa60-4eec-43fc-9294-46ec5c81cfda for country-leaders.onrender.com/>]>


Try to query the countries endpoint using the cookie, save the output and print it.

In [7]:
# query the /countries endpoint, assign the output to the countries variable (1 line)
countries = requests.get(countries_url, cookies=cookies).json()

# display the countries variable (1 line)
print(countries)

['us', 'be', 'ma', 'ru', 'fr']


Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### Getting the actual data from the API

Query the `/leaders` endpoint.

In [8]:
# Set the leaders_url variable (1 line)
leaders_url = f"{root_url}/leaders"

# query the /leaders endpoint, assign the output to the leaders variable (1 line)
leaders = requests.get(leaders_url, cookies=cookies).json()

# display the leaders variable (1 line)
print(leaders)

{'message': 'Please specify a country'}


In [ ]:
'''
The code with the special parametr
# Set the leaders_url variable (1 line)
leaders_url = f"{root_url}/leaders"

# query the /leaders endpoint, assign the output to the leaders variable (!!!refresh cookie first if necessary!!!) (1 line)
leaders = requests.get(leaders_url, cookies=cookies, params={"country": first_country}).json()

# display the leaders variable (1 line)
print(leaders)
'''

In [ ]:
'''
# The code with refreshing coocie
# Refresh the cookie by querying the /cookie endpoint
req = requests.get(cookie_url)
cookies = req.cookies  # Update the cookies variable with the new cookie
print("New cookie obtained:", cookies)

# Query the /countries endpoint using the refreshed cookie
countries = requests.get(countries_url, cookies=cookies).json()
print("Countries:", countries)

# Set the leaders_url variable
leaders_url = f"{root_url}/leaders"

# Query the /leaders endpoint using the refreshed cookie and parameters (using the first country as an example)
first_country = countries[0] if isinstance(countries, list) else list(countries.keys())[0]
leaders = requests.get(leaders_url, cookies=cookies, params={"country": first_country}).json()

# Display the leaders variable
print("Leaders:", leaders)
''' 

It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.onrender.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [9]:
# query the /leaders endpoint using cookies and parameters (take any country in countries)
# assign the output to the leaders variable (1 line)
leaders = requests.get(leaders_url, cookies=cookies, params={"country": countries[0]}).json()

# display the leaders variable (1 line)
print(leaders)

[{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'place_of_bi

### A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each `json` result in a dictionary called `leaders_per_country`.

In [10]:
# 4 lines
# Initialize an empty dictionary to store leaders data for each country
leaders_per_country = {}

# Loop through each country in the countries list and query the /leaders endpoint
for country in countries:
    leaders_per_country[country] = requests.get(leaders_url, cookies=cookies, params={"country": country}).json()

# Display the dictionary with leaders data for each country
print(leaders_per_country)


{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'plac

In [11]:
# or 1 line
leaders_per_country = {country: requests.get(leaders_url, cookies=requests.get(cookie_url).cookies, params={"country": country}).json() for country in countries}


It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [12]:
# < 15 lines
def get_leaders():
    # Define the URLs
    root_url = "https://country-leaders.onrender.com"
    leaders_url = f"{root_url}/leaders"
    cookie_url = f"{root_url}/cookie"
    countries_url = f"{root_url}/countries"
    
    # Get the cookies
    cookies = requests.get(cookie_url).cookies
    
    # Get the countries
    countries = requests.get(countries_url, cookies=cookies).json()
    
    # Initialize dictionary to store leaders data
    leaders_per_country = {
        country: requests.get(leaders_url, cookies=cookies, params={"country": country}).json()
        for country in countries
    }
    
    # Return the dictionary
    return leaders_per_country


Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [13]:
# 2 lines
# Test the get_leaders function and save the result in leaders_per_country
leaders_per_country = get_leaders()

# Display the leaders_per_country dictionary
print(leaders_per_country)

{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'plac

## Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [14]:
# 3 lines
# USA
# Get the Wikipedia URL of the first leader (example)
wiki_url = leaders_per_country['us'][0]['wikipedia_url']  # Adjust the country and key if needed

# Query the Wikipedia page
response = requests.get(wiki_url)

# Display the text of the page
print(response.text)

'''
Tips
leaders_per_country['us'] is a list containing leader dictionaries.  
leaders_per_country['us'][0] accesses the first leader in that list.  
leaders_per_country['us'][0]['wikipedia_url'] retrieves the Wikipedia URL of that leader.

# Print the details of the first leader for the 'us' country
print(leaders_per_country['us'][0])  # Assuming it's a list of leaders

# Parse a link
print(leaders_per_country['be'][0]['wikipedia_url'])
'''


<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" lang="en" dir="ltr">
<head>
<meta charset="UTF-8">
<title>George Washington - Wikipedia</title>
<script>(function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector

"\nTips\nleaders_per_country['us'] is a list containing leader dictionaries.  \nleaders_per_country['us'][0] accesses the first leader in that list.  \nleaders_per_country['us'][0]['wikipedia_url'] retrieves the Wikipedia URL of that leader.\n\n# Print the details of the first leader for the 'us' country\nprint(leaders_per_country['us'][0])  # Assuming it's a list of leaders\n\n# Parse a link\nprint(leaders_per_country['be'][0]['wikipedia_url'])\n"

In [21]:
# Get the Wikipedia URL of the first leader (example)
# Belgia
wiki_url = leaders_per_country['be'][0]['wikipedia_url']  # Access the 'wikipedia_url' key

# Query the Wikipedia page
response = requests.get(wiki_url)

# Display the text of the page
print(response.text)

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" lang="nl" dir="ltr">
<head>
<meta charset="UTF-8">
<title>Guy Verhofstadt - Wikipedia</title>
<script>(function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-f

In [16]:
# Get the Wikipedia URL of the first leader (example)
# Marokko
wiki_url = leaders_per_country['ma'][0]['wikipedia_url']  # Access the 'wikipedia_url' key

# Query the Wikipedia page
response = requests.get(wiki_url)

# Display the text of the page
print(response.text)

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-disabled skin-theme-clientpref-day vector-toc-available" lang="ar" dir="rtl">
<head>
<meta charset="UTF-8">
<title>محمد السادس بن الحسن - ويكيبيديا</title>
<script>(function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 ve

In [17]:
# Get the Wikipedia URL of the first leader (example)
# rusha
wiki_url = leaders_per_country['ru'][2]['wikipedia_url']  # Access the 'wikipedia_url' key

# Query the Wikipedia page
response = requests.get(wiki_url)

# Display the text of the page
print(response.text)


<!DOCTYPE html>
<html class="client-nojs" lang="ru" dir="ltr">
<head>
<meta charset="UTF-8">
<title>Ельцин, Борис Николаевич — Википедия</title>
<script>(function(){var className="client-js";var cookie=document.cookie.match(/(?:^|; )ruwikimwclientpreferences=([^;]+)/);if(cookie){cookie[1].split('%2C').forEach(function(pref){className=className.replace(new RegExp('(^| )'+pref.replace(/-clientpref-\w+$|[^\w-]+/g,'')+'-clientpref-\\w+( |$)'),'$1'+pref+'$2');});}document.documentElement.className=className;}());RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\t."," \t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","январь","февраль","март","апрель","май","июнь","июль","август","сентябрь","октябрь","ноябрь","декабрь"],"wgRequestId":"8258494d-e40c-4713-b6ce-d514061e9331","wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Ельцин,_Борис_Николаевич","wgTitle":"Ельцин, Борис Николаевич","wgCurRevisionId

In [26]:
# Get the Wikipedia URL of the first leader (example)
# France
wiki_url = leaders_per_country['fr'][2]['wikipedia_url']  # Access the 'wikipedia_url' key

# Query the Wikipedia page
response = requests.get(wiki_url)

# Display the text of the page
print(response.text)

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" lang="fr" dir="ltr">
<head>
<meta charset="UTF-8">
<title>François Mitterrand — Wikipédia</title>
<script>(function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vect

Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function and print it to take a look. You will start the actual parsing in the next step.

In [27]:
# 3 lines
from bs4 import BeautifulSoup  # Import the BeautifulSoup library

soup = BeautifulSoup(response.text, 'html.parser')  # Parse the raw HTML text

print(soup.prettify())  # Print the prettified HTML for inspection

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" dir="ltr" lang="fr">
 <head>
  <meta charset="utf-8"/>
  <title>
   François Mitterrand — Wikipédia
  </title>
  <script>
   (function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-widt

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [32]:
# Find all <p> tags (paragraphs) in the HTML
paragraphs = soup.find_all('p')

# Find the first non-empty paragraph and print its text
print(next(paragraph.get_text() for paragraph in paragraphs if paragraph.get_text().strip()))


« Mitterrand » redirige ici.  Pour les autres significations, voir Mitterrand (homonymie).



If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one
  * store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
  * exit the loop

In [30]:
# less than 10 lines
# Loop through paragraphs to find the first meaningful one
first_paragraph = ""
for paragraph in paragraphs:
    text = paragraph.get_text().strip()
    if text:  # Check if paragraph is non-empty
        first_paragraph = text
        break  # Exit after finding the first meaningful paragraph

print(first_paragraph)

« Mitterrand » redirige ici.  Pour les autres significations, voir Mitterrand (homonymie).


At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [31]:
# more than 10 lines
import requests
from bs4 import BeautifulSoup

def get_first_paragraph(wikipedia_url):
    print(wikipedia_url)  # Keep this for the rest of the notebook
    response = requests.get(wikipedia_url)
    soup = BeautifulSoup(response.text, 'html.parser')
    first_paragraph = ""
    for paragraph in soup.find_all('p'):
        text = paragraph.get_text().strip()
        if text:
            first_paragraph = text
            break  # Exit after finding the first meaningful paragraph
    return first_paragraph


In [32]:
# 3 lines
# Example Wikipedia URL
wiki_url = "https://ru.wikipedia.org/wiki/%D0%95%D0%BB%D1%8C%D1%86%D0%B8%D0%BD,_%D0%91%D0%BE%D1%80%D0%B8%D1%81_%D0%9D%D0%B8%D0%BA%D0%BE%D0%BB%D0%B0%D0%B5%D0%B2%D0%B8%D1%87"

# Get the first paragraph
first_paragraph = get_first_paragraph(wiki_url)

# Display the result
print(first_paragraph)


https://ru.wikipedia.org/wiki/%D0%95%D0%BB%D1%8C%D1%86%D0%B8%D0%BD,_%D0%91%D0%BE%D1%80%D0%B8%D1%81_%D0%9D%D0%B8%D0%BA%D0%BE%D0%BB%D0%B0%D0%B5%D0%B2%D0%B8%D1%87
Бори́с Никола́евич Е́льцин (1 февраля 1931 (1931-02-01), Бутка, Буткинский район, Уральская область, РСФСР, СССР — 23 апреля 2007, Москва, Россия) — советский и российский партийный, государственный и политический деятель, первый всенародно избранный Президент Российской Федерации (1991—1999)➤; в ноябре 1991 — июне 1992 года одновременно возглавлял правительство. С марта по май 1992 года исполнял обязанности министра обороны Российской Федерации.


### Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [33]:
# 3 lines
import re

def sanitize_text(text):
    # Remove citations like [1], [2], etc.
    text = re.sub(r'\[\d+\]', '', text)
    
    # Remove pronunciation guides or content within parentheses (e.g., phonetics, IPA)
    text = re.sub(r'\(.*?\)', '', text)
    
    # Remove any remaining HTML tags
    text = re.sub(r'<.*?>', '', text)
    
    # Remove extra whitespace
    text = re.sub(r'\s+', ' ', text).strip()
    
    return text

In [34]:
sanitized_text = sanitize_text(first_paragraph)
print(sanitized_text)


Бори́с Никола́евич Е́льцин , Бутка, Буткинский район, Уральская область, РСФСР, СССР — 23 апреля 2007, Москва, Россия) — советский и российский партийный, государственный и политический деятель, первый всенародно избранный Президент Российской Федерации ➤; в ноябре 1991 — июне 1992 года одновременно возглавлял правительство. С марта по май 1992 года исполнял обязанности министра обороны Российской Федерации.


Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [35]:
# NOT in 10 lines
import requests
from bs4 import BeautifulSoup
import re

def get_first_paragraph(wikipedia_url):
    print(wikipedia_url)  # Keep this for reference
    
    response = requests.get(wikipedia_url)
    soup = BeautifulSoup(response.text, 'html.parser')
    
    first_paragraph = ""
    for paragraph in soup.find_all('p'):
        text = paragraph.get_text().strip()
        if text:
            first_paragraph = text
            break
    
    # Apply regex to clean the first paragraph
    first_paragraph = re.sub(r'\[\d+\]', '', first_paragraph)  # Remove citations like [1], [2]
    first_paragraph = re.sub(r'\(.*?\)', '', first_paragraph)  # Remove content within parentheses
    first_paragraph = re.sub(r'\s+', ' ', first_paragraph).strip()  # Clean up extra spaces

    return first_paragraph


Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [36]:
# < 20 lines
import requests
from bs4 import BeautifulSoup
import re

def get_first_paragraph(wikipedia_url):
    print(wikipedia_url)  # Reference for tracking

    response = requests.get(wikipedia_url)
    soup = BeautifulSoup(response.text, 'html.parser')

    first_paragraph = ""
    for paragraph in soup.find_all('p'):
        text = paragraph.get_text().strip()
        if text:
            first_paragraph = text
            break

    # Sanitize the text using regex patterns
    first_paragraph = re.sub(r'\[\d+\]', '', first_paragraph)  # Remove citations
    first_paragraph = re.sub(r'\(.*?\)', '', first_paragraph)   # Remove parentheses content
    first_paragraph = re.sub(r'<.*?>', '', first_paragraph)     # Remove HTML tags
    first_paragraph = re.sub(r'[*†]', '', first_paragraph)      # Remove unwanted symbols
    first_paragraph = re.sub(r'\s+', ' ', first_paragraph).strip()  # Clean up extra whitespace

    return first_paragraph


## Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [39]:
# < 20 lines
import requests

def get_leaders():
    # Set up the URLs
    root_url = "https://country-leaders.onrender.com"
    cookie_url = f"{root_url}/cookie"
    countries_url = f"{root_url}/countries"
    leaders_url = f"{root_url}/leaders"

    # Function to refresh cookies
    def refresh_cookies():
        return requests.get(cookie_url).cookies

    # Initial cookie setup
    cookies = refresh_cookies()

    # Get the list of countries
    countries = requests.get(countries_url, cookies=cookies).json()
    leaders_per_country = {}

    # Loop over each country
    for country in countries:
        response = requests.get(leaders_url, cookies=cookies, params={"country": country})
        
        # Check for cookie expiration and refresh if needed
        if response.status_code == 401 and 'expired' in response.json().get('message', '').lower():
            cookies = refresh_cookies()
            response = requests.get(leaders_url, cookies=cookies, params={"country": country})

        leaders = response.json()

        # Loop over each leader to get their bio
        for leader in leaders:
            wikipedia_url = leader.get("wikipedia_url")
            if wikipedia_url:
                leader["bio"] = get_first_paragraph(wikipedia_url)

        leaders_per_country[country] = leaders

    return leaders_per_country

In [40]:
# Check the output of your function (2 lines)
leaders_per_country = get_leaders()
print(leaders_per_country)


https://en.wikipedia.org/wiki/George_Washington
https://en.wikipedia.org/wiki/Barack_Obama
https://en.wikipedia.org/wiki/Abraham_Lincoln
https://en.wikipedia.org/wiki/George_W._Bush
https://en.wikipedia.org/wiki/Bill_Clinton
https://en.wikipedia.org/wiki/Joe_Biden
https://en.wikipedia.org/wiki/Franklin_D._Roosevelt
https://en.wikipedia.org/wiki/Andrew_Johnson
https://en.wikipedia.org/wiki/Gerald_Ford
https://en.wikipedia.org/wiki/Richard_Nixon
https://en.wikipedia.org/wiki/Lyndon_B._Johnson
https://en.wikipedia.org/wiki/John_F._Kennedy
https://en.wikipedia.org/wiki/Dwight_D._Eisenhower
https://en.wikipedia.org/wiki/Ronald_Reagan
https://en.wikipedia.org/wiki/Harry_S._Truman
https://en.wikipedia.org/wiki/John_Adams
https://en.wikipedia.org/wiki/Thomas_Jefferson
https://en.wikipedia.org/wiki/James_Madison
https://en.wikipedia.org/wiki/James_Monroe
https://en.wikipedia.org/wiki/John_Quincy_Adams


ConnectTimeout: HTTPSConnectionPool(host='en.wikipedia.org', port=443): Max retries exceeded with url: /wiki/John_Quincy_Adams (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x000002C89011DD90>, 'Connection to en.wikipedia.org timed out. (connect timeout=None)'))

Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function with an *exception* or check if the `status_code` is a cookie error. In either case, get new cookies and query the api again.

If your code did not crash,

In [53]:
import requests

def get_leaders():
    # Set up the URLs
    root_url = "https://country-leaders.onrender.com"
    cookie_url = f"{root_url}/cookie"
    countries_url = f"{root_url}/countries"
    leaders_url = f"{root_url}/leaders"

    # Function to refresh cookies
    def refresh_cookies():
        return requests.get(cookie_url).cookies

    # Initial cookie setup
    cookies = refresh_cookies()

    # Get the list of countries
    countries = requests.get(countries_url, cookies=cookies).json()
    leaders_per_country = {}

    # Loop over each country
    for country in countries:
        try:
            response = requests.get(leaders_url, cookies=cookies, params={"country": country})

            # Check for cookie expiration and refresh if needed
            if response.status_code == 401:
                cookies = refresh_cookies()
                response = requests.get(leaders_url, cookies=cookies, params={"country": country})

            # Ensure response is a list before processing
            if isinstance(response.json(), list):
                leaders = response.json()

                # Loop over each leader to get their bio
                for leader in leaders:
                    wikipedia_url = leader.get("wikipedia_url")
                    if wikipedia_url:
                        leader["bio"] = get_first_paragraph(wikipedia_url)

                leaders_per_country[country] = leaders

        except (requests.exceptions.RequestException, KeyError, ValueError) as e:
            print(f"An error occurred for {country}: {e}")

    return leaders_per_country

Check the output of your function again.

In [54]:
# Check the output of your function (1 line)
print(get_leaders())

https://en.wikipedia.org/wiki/George_Washington
https://en.wikipedia.org/wiki/Barack_Obama
https://en.wikipedia.org/wiki/Abraham_Lincoln
https://en.wikipedia.org/wiki/George_W._Bush
https://en.wikipedia.org/wiki/Bill_Clinton
https://en.wikipedia.org/wiki/Joe_Biden
https://en.wikipedia.org/wiki/Franklin_D._Roosevelt
https://en.wikipedia.org/wiki/Andrew_Johnson
An error occurred for us: HTTPSConnectionPool(host='en.wikipedia.org', port=443): Max retries exceeded with url: /wiki/Andrew_Johnson (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x000002C890D88D10>, 'Connection to en.wikipedia.org timed out. (connect timeout=None)'))
https://nl.wikipedia.org/wiki/Guy_Verhofstadt
https://nl.wikipedia.org/wiki/Yves_Leterme
https://nl.wikipedia.org/wiki/Herman_Van_Rompuy
https://nl.wikipedia.org/wiki/L%C3%A9on_Delacroix
https://nl.wikipedia.org/wiki/Henri_Carton_de_Wiart
https://nl.wikipedia.org/wiki/Georges_Theunis
https://nl.wikipedia.org/wiki/Aloys_Van_de_Vyvere
ht

Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [55]:
# < 20 lines
import requests
from bs4 import BeautifulSoup
import re

def get_first_paragraph(wikipedia_url, session):
    print(wikipedia_url)  # Keep this for tracking progress
    try:
        response = session.get(wikipedia_url)
        response.raise_for_status()  # Raise an error for bad status codes
        soup = BeautifulSoup(response.text, 'html.parser')

        # Loop over paragraphs to find the first relevant one
        for paragraph in soup.find_all('p'):
            text = paragraph.get_text().strip()
            if text:
                # Sanitize with regex
                text = re.sub(r'\[.*?\]|\{.*?\}|\(.*?\)|<.*?>', '', text)
                return text
    except (requests.exceptions.RequestException, ValueError) as e:
        print(f"An error occurred while fetching {wikipedia_url}: {e}")
    return None


Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [56]:
# <25 lines
def get_leaders():
    # Set up the URLs
    root_url = "https://country-leaders.onrender.com"
    cookie_url = f"{root_url}/cookie"
    countries_url = f"{root_url}/countries"
    leaders_url = f"{root_url}/leaders"

    # Function to refresh cookies
    def refresh_cookies():
        return requests.get(cookie_url).cookies

    # Initial cookie setup
    cookies = refresh_cookies()
    countries = requests.get(countries_url, cookies=cookies).json()
    leaders_per_country = {}

    # Use a session to make multiple requests efficiently
    with requests.Session() as session:
        session.cookies.update(cookies)
        for country in countries:
            try:
                response = session.get(leaders_url, params={"country": country})
                if response.status_code == 401:
                    cookies = refresh_cookies()
                    session.cookies.update(cookies)
                    response = session.get(leaders_url, params={"country": country})

                if isinstance(response.json(), list):
                    leaders = response.json()
                    for leader in leaders:
                        wikipedia_url = leader.get("wikipedia_url")
                        if wikipedia_url:
                            leader["bio"] = get_first_paragraph(wikipedia_url, session)
                    leaders_per_country[country] = leaders

            except (requests.exceptions.RequestException, KeyError, ValueError) as e:
                print(f"An error occurred for {country}: {e}")

    return leaders_per_country


Test your new functions.



In [57]:
# Run the get_leaders function and print the results for testing
leaders_per_country = get_leaders()

# Print a summary of the results
for country, leaders in leaders_per_country.items():
    print(f"\nCountry: {country}")
    for leader in leaders[:2]:  # Display the first 2 leaders per country for brevity
        print(f"Name: {leader.get('name')}")
        print(f"Bio: {leader.get('bio')[:100]}...")  # Print the first 100 characters of the bio


https://en.wikipedia.org/wiki/George_Washington
https://en.wikipedia.org/wiki/Barack_Obama
https://en.wikipedia.org/wiki/Abraham_Lincoln
https://en.wikipedia.org/wiki/George_W._Bush
https://en.wikipedia.org/wiki/Bill_Clinton
https://en.wikipedia.org/wiki/Joe_Biden
https://en.wikipedia.org/wiki/Franklin_D._Roosevelt
https://en.wikipedia.org/wiki/Andrew_Johnson
https://en.wikipedia.org/wiki/Gerald_Ford
https://en.wikipedia.org/wiki/Richard_Nixon
https://en.wikipedia.org/wiki/Lyndon_B._Johnson
https://en.wikipedia.org/wiki/John_F._Kennedy
https://en.wikipedia.org/wiki/Dwight_D._Eisenhower
https://en.wikipedia.org/wiki/Ronald_Reagan
https://en.wikipedia.org/wiki/Harry_S._Truman
https://en.wikipedia.org/wiki/John_Adams
https://en.wikipedia.org/wiki/Thomas_Jefferson
https://en.wikipedia.org/wiki/James_Madison
https://en.wikipedia.org/wiki/James_Monroe
https://en.wikipedia.org/wiki/John_Quincy_Adams
https://en.wikipedia.org/wiki/Andrew_Jackson
https://en.wikipedia.org/wiki/Martin_Van_Buren
ht

## Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Check out the `with` statement.

In [58]:
# 3 lines
import json

with open('leaders.json', 'w', encoding='utf-8') as file:
    json.dump(leaders_per_country, file, ensure_ascii=False, indent=4)


Make sure the file can be read back. Write the code to read the file. And check the variables are the same.

In [59]:
# 3 lines
# Read the leaders.json file
with open('leaders.json', 'r', encoding='utf-8') as file:
    loaded_leaders = json.load(file)

# Check if the loaded data matches the original
print(loaded_leaders == leaders_per_country)  # This should print True if they are the same


True


Make a function `save(leaders_per_country)` to call this code easily.

In [60]:
# 3 lines
import json

def save(leaders_per_country):
    with open('leaders.json', 'w', encoding='utf-8') as file:
        json.dump(leaders_per_country, file, ensure_ascii=False, indent=4)


In [61]:
# Call the function (1 line)
save(leaders_per_country)


## Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## To go further

If you want to practice scraping, you can read this section and tackle the exercise.

You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!